In [3]:
import pandas as pd

# imports
import pandas as pd
import seaborn as sns
import statsmodels.formula.api as smf
from sklearn.linear_model import LinearRegression
from sklearn import metrics
from sklearn.model_selection import train_test_split
import numpy as np
import mlflow
# allow plots to appear directly in the notebook
%matplotlib inline

In [4]:
orders_df = pd.read_csv('order_data/order_data_2016-01-02', sep='\t')
orders_df.columns = ['order_id', 'driver_id', 'passenger_id', 'start_region_hash', 'dest_region_hash', 'price' , 'time']
print(orders_df.head())

FileNotFoundError: [Errno 2] No such file or directory: 'order_data/order_data_2016-01-02'

In [27]:
import datetime
def map_to_slot(date_time):
    # Extract the hour and minute from the date and time
    hour = date_time.hour
    minute = date_time.minute

    # Calculate the slot number (0-23)
    slot = hour
    if minute >= 30:
        slot += 1
    
    # Ensure that the slot number is within the range 0-23
    if slot >= 24:
        slot = 0

    return slot

In [28]:
# Convert the 'date' column to datetime type
orders_df['time'] = pd.to_datetime(orders_df['time'])

# Map each date and time to a slot number
orders_df['slots'] = orders_df['time'].apply(map_to_slot)

# Display the resulting DataFrame
print(orders_df.head())

                           order_id                         driver_id  \
0  43714872775226b9dc8d859d3a87e4bf  84bae8f17655c03c851b39f968128adf   
1  5ddb72e811a06dcda166c51a83ee2d05  52de30cc588fde1c3c4e74500f82e693   
2  5f50af9744e4aecc9fb81189f278287f  bfb4b43d2024fa7c3a4645efbeed4ffb   
3  d1ea51bf27e5c6f15bfe6d2ad060649a  6e5ec574091b161fd53ab9312036a5e0   
4  960fcaead9153749cdd490114a47f138  af311d469408fe102327164b631e45af   

                       passenger_id                 start_region_hash  \
0  4cc22b6c8cbfa7a3a94c0219dcadf68d  d4ec2125aff74eded207d2d915ef682f   
1  2c1ef59660add477f2639817f2c20947  b26a240205c852804ff8758628c0a86a   
2  6afb7d8210b1f273e5b4161605fa67b6  82cc4851f9e4faa4e54309f8bb73fd7c   
3  dca186500f58753bd76bd395f246d701  364bf755f9b270f0f9141d1a61de43ee   
4  f421d6262e3219b3722ae3f74028aca2  4f8d81b5c31af5d1ba579a65ddc8a5cb   

                   dest_region_hash  price                time  slots  
0  2920ece99323b4c111d6f9affc7ea034   18.0 2016-01

In [29]:
# Convert the timestamp column to datetime objects
orders_df['time'] = pd.to_datetime(orders_df['time'])

# Map day of the week to numbers 1-7 (Monday-Sunday)
orders_df['day_of_week'] = orders_df['time'].dt.weekday + 1

# Display the resulting DataFrame
print(orders_df.head())

                           order_id                         driver_id  \
0  43714872775226b9dc8d859d3a87e4bf  84bae8f17655c03c851b39f968128adf   
1  5ddb72e811a06dcda166c51a83ee2d05  52de30cc588fde1c3c4e74500f82e693   
2  5f50af9744e4aecc9fb81189f278287f  bfb4b43d2024fa7c3a4645efbeed4ffb   
3  d1ea51bf27e5c6f15bfe6d2ad060649a  6e5ec574091b161fd53ab9312036a5e0   
4  960fcaead9153749cdd490114a47f138  af311d469408fe102327164b631e45af   

                       passenger_id                 start_region_hash  \
0  4cc22b6c8cbfa7a3a94c0219dcadf68d  d4ec2125aff74eded207d2d915ef682f   
1  2c1ef59660add477f2639817f2c20947  b26a240205c852804ff8758628c0a86a   
2  6afb7d8210b1f273e5b4161605fa67b6  82cc4851f9e4faa4e54309f8bb73fd7c   
3  dca186500f58753bd76bd395f246d701  364bf755f9b270f0f9141d1a61de43ee   
4  f421d6262e3219b3722ae3f74028aca2  4f8d81b5c31af5d1ba579a65ddc8a5cb   

                   dest_region_hash  price                time  slots  \
0  2920ece99323b4c111d6f9affc7ea034   18.0 2016-0

In [30]:
grouped_data_origin = orders_df.groupby('start_region_hash').size()
print(grouped_data_origin)

start_region_hash
08232402614a9b48895cc3d0aeb0e9f2      235
08f5b445ec6b29deba62e6fd8b0325a6      457
0a5fef95db34383403d11cb6af937309       78
1afd7afbc81ecc1b13886a569d869e8a    10637
1c60154546102e6525f68cb4f31e0657      577
                                    ...  
f2c8c4bb99e6377d21de71275afd6cd2     2095
f47f35242ed40655814bc086d7514046      965
f9280c5dab6910ed44e518248048b9fe      760
fc34648599753c9e74ab238e9a4a07ad     6666
fff4e8465d1e12621bc361276b6217cf      257
Length: 66, dtype: int64


In [31]:

# Group the data by the 'Entry' column
grouped_data = orders_df.groupby(['start_region_hash', 'slots'])

for name, group in grouped_data:
    print(name)
    print(group)



('08232402614a9b48895cc3d0aeb0e9f2', 0)
                                order_id                         driver_id  \
17178   04b90ce3b94dca07e1e6d35684997a28  21151cf2fef375579e05d3cfc09507b5   
274627  483168b43163d6e1aa20c9291fdef4c6                               NaN   

                            passenger_id                 start_region_hash  \
17178   cbfe259e4f3c611eaa11ce86ca9a7133  08232402614a9b48895cc3d0aeb0e9f2   
274627  cbfe259e4f3c611eaa11ce86ca9a7133  08232402614a9b48895cc3d0aeb0e9f2   

                        dest_region_hash  price                time  slots  \
17178   3e12208dd0be281c92a6ab57d9a6fb32   30.0 2016-01-02 23:48:09      0   
274627  3e12208dd0be281c92a6ab57d9a6fb32   30.0 2016-01-02 23:39:54      0   

        day_of_week  
17178             6  
274627            6  
('08232402614a9b48895cc3d0aeb0e9f2', 1)
                                order_id                         driver_id  \
199427  53b16e3d4a009aaad2534697423a1a40  f4bfa263735558aa6bcdf5b352308

In [32]:
sizeOfEachSlot  = grouped_data.size();
sizeOfEachSlot.to_csv('regionSlotRequestsTotal.csv')

print(sizeOfEachSlot)

start_region_hash                 slots
08232402614a9b48895cc3d0aeb0e9f2  0         2
                                  1         1
                                  2         1
                                  6         1
                                  7         2
                                           ..
fff4e8465d1e12621bc361276b6217cf  19       17
                                  20       18
                                  21        8
                                  22       15
                                  23       11
Length: 1475, dtype: int64


In [33]:
#grouped_driver_data = orders_df.groupby('slots').groupby('driver_id').size();
grouped_driver_data = orders_df.groupby(['start_region_hash','slots', 'driver_id'])
print(grouped_driver_data.size())



start_region_hash                 slots  driver_id                       
08232402614a9b48895cc3d0aeb0e9f2  0      21151cf2fef375579e05d3cfc09507b5    1
                                  1      f4bfa263735558aa6bcdf5b352308259    1
                                  6      fd32ed8daac0024461c703ba002f4633    1
                                  7      01510dda5582c2582705129048715c19    1
                                         25698ff9159aee8229e6131c13c4991f    1
                                                                            ..
fff4e8465d1e12621bc361276b6217cf  23     6c7e38a21a27ad10919af8a3e60c377a    2
                                         a6a28ce754aa5ed793656d969e49284a    1
                                         adf7bc9408ba89bfef741e01f6ef5fa7    1
                                         b6d90050b7a8b9f5e78a9d66777117f6    1
                                         fd41a084d58c1e241e5f62432e4dbba7    1
Length: 223269, dtype: int64


In [34]:
grouped_df = pd.read_csv('grouped_data_driver.csv')
print(grouped_df.head())

                  start_region_hash  slots                         driver_id  \
0  08232402614a9b48895cc3d0aeb0e9f2      0  11684580a489ec0919abccf786734183   
1  08232402614a9b48895cc3d0aeb0e9f2      0  8dfbc82a7b0e90da3a91f1a21dd25304   
2  08232402614a9b48895cc3d0aeb0e9f2      1  070bb394315547c4cce18588a1d5a1ea   
3  08232402614a9b48895cc3d0aeb0e9f2      1  101a329632f70644d272ce1199932025   
4  08232402614a9b48895cc3d0aeb0e9f2      1  52625b4c4cbf4679c484d14499cd78de   

   0  
0  1  
1  1  
2  1  
3  1  
4  1  


In [35]:
grouped_driver_slots = grouped_df.groupby(['start_region_hash','slots']).size();
grouped_driver_slots.to_csv('pickedRequestTotal.csv')
print(grouped_driver_slots)

start_region_hash                 slots
08232402614a9b48895cc3d0aeb0e9f2  0         2
                                  1         3
                                  2         1
                                  4         1
                                  6         1
                                           ..
fff4e8465d1e12621bc361276b6217cf  19       13
                                  20       14
                                  21       10
                                  22       14
                                  23        8
Length: 1498, dtype: int64


In [36]:
# Load the first data frame
df1 = pd.read_csv('regionSlotRequestsTotal.csv')

# Load the second data frame
df2 = pd.read_csv('pickedRequestTotal.csv')

# Join the two data frames on the 'ID' and 'Name' columns
df_merged = pd.merge(df1, df2, on=['start_region_hash', 'slots'], how='left')
print(df_merged.head())

                  start_region_hash  slots  0_x  0_y
0  08232402614a9b48895cc3d0aeb0e9f2      0    2  2.0
1  08232402614a9b48895cc3d0aeb0e9f2      1    1  3.0
2  08232402614a9b48895cc3d0aeb0e9f2      2    1  1.0
3  08232402614a9b48895cc3d0aeb0e9f2      6    1  1.0
4  08232402614a9b48895cc3d0aeb0e9f2      7    2  3.0


In [37]:
# Replace NaN values with 0
df_merged['0_y'] = df_merged['0_y'].fillna(0)
print(df_merged)


                     start_region_hash  slots  0_x   0_y
0     08232402614a9b48895cc3d0aeb0e9f2      0    2   2.0
1     08232402614a9b48895cc3d0aeb0e9f2      1    1   3.0
2     08232402614a9b48895cc3d0aeb0e9f2      2    1   1.0
3     08232402614a9b48895cc3d0aeb0e9f2      6    1   1.0
4     08232402614a9b48895cc3d0aeb0e9f2      7    2   3.0
...                                ...    ...  ...   ...
1470  fff4e8465d1e12621bc361276b6217cf     19   17  13.0
1471  fff4e8465d1e12621bc361276b6217cf     20   18  14.0
1472  fff4e8465d1e12621bc361276b6217cf     21    8  10.0
1473  fff4e8465d1e12621bc361276b6217cf     22   15  14.0
1474  fff4e8465d1e12621bc361276b6217cf     23   11   8.0

[1475 rows x 4 columns]


In [38]:
# Subtract 'column1' from 'column2' and write the result to 'column3'
df_merged['gap'] = df_merged['0_x'] - df_merged['0_y']
print(df_merged)

                     start_region_hash  slots  0_x   0_y  gap
0     08232402614a9b48895cc3d0aeb0e9f2      0    2   2.0  0.0
1     08232402614a9b48895cc3d0aeb0e9f2      1    1   3.0 -2.0
2     08232402614a9b48895cc3d0aeb0e9f2      2    1   1.0  0.0
3     08232402614a9b48895cc3d0aeb0e9f2      6    1   1.0  0.0
4     08232402614a9b48895cc3d0aeb0e9f2      7    2   3.0 -1.0
...                                ...    ...  ...   ...  ...
1470  fff4e8465d1e12621bc361276b6217cf     19   17  13.0  4.0
1471  fff4e8465d1e12621bc361276b6217cf     20   18  14.0  4.0
1472  fff4e8465d1e12621bc361276b6217cf     21    8  10.0 -2.0
1473  fff4e8465d1e12621bc361276b6217cf     22   15  14.0  1.0
1474  fff4e8465d1e12621bc361276b6217cf     23   11   8.0  3.0

[1475 rows x 5 columns]


In [39]:
# Rename the 'column1' and 'column2' columns
df_merged = df_merged.rename(columns={'0_x': 'demand', '0_y': 'picked'})
print(df_merged)


                     start_region_hash  slots  demand  picked  gap
0     08232402614a9b48895cc3d0aeb0e9f2      0       2     2.0  0.0
1     08232402614a9b48895cc3d0aeb0e9f2      1       1     3.0 -2.0
2     08232402614a9b48895cc3d0aeb0e9f2      2       1     1.0  0.0
3     08232402614a9b48895cc3d0aeb0e9f2      6       1     1.0  0.0
4     08232402614a9b48895cc3d0aeb0e9f2      7       2     3.0 -1.0
...                                ...    ...     ...     ...  ...
1470  fff4e8465d1e12621bc361276b6217cf     19      17    13.0  4.0
1471  fff4e8465d1e12621bc361276b6217cf     20      18    14.0  4.0
1472  fff4e8465d1e12621bc361276b6217cf     21       8    10.0 -2.0
1473  fff4e8465d1e12621bc361276b6217cf     22      15    14.0  1.0
1474  fff4e8465d1e12621bc361276b6217cf     23      11     8.0  3.0

[1475 rows x 5 columns]


In [40]:
clusters_df = pd.read_csv('cluster_map/cluster_map', sep='\t')
clusters_df.columns = ['start_region_hash','region_id']
print(clusters_df)

                   start_region_hash  region_id
0   f2c8c4bb99e6377d21de71275afd6cd2          2
1   58c7a4888306d8ff3a641d1c0feccbe3          3
2   b26a240205c852804ff8758628c0a86a          4
3   4b9e4cf2fbdc8281b8a1f9f12b80ce4d          5
4   1cbfbdd079ef93e74405c53fcfff8567          6
..                               ...        ...
60  a735449c5c09df639c35a7d61fad3ee5         62
61  0a5fef95db34383403d11cb6af937309         63
62  bf44d327f0232325c6d5280926d7b37d         64
63  825a21aa308dea206adb49c4b77c7805         65
64  1ecbb52d73c522f184a6fc53128b1ea1         66

[65 rows x 2 columns]


In [41]:
# Merge the DataFrames on the 'column1' and 'column2' columns
# final_df = pd.merge(df_merged, clusters_df, left_on='start_region_hash', right_on='region_hash')
final_df = pd.merge(df_merged, clusters_df, on='start_region_hash')
print(final_df)

                     start_region_hash  slots  demand  picked  gap  region_id
0     08232402614a9b48895cc3d0aeb0e9f2      0       2     2.0  0.0         50
1     08232402614a9b48895cc3d0aeb0e9f2      1       1     3.0 -2.0         50
2     08232402614a9b48895cc3d0aeb0e9f2      2       1     1.0  0.0         50
3     08232402614a9b48895cc3d0aeb0e9f2      6       1     1.0  0.0         50
4     08232402614a9b48895cc3d0aeb0e9f2      7       2     3.0 -1.0         50
...                                ...    ...     ...     ...  ...        ...
1446  fff4e8465d1e12621bc361276b6217cf     19      17    13.0  4.0         32
1447  fff4e8465d1e12621bc361276b6217cf     20      18    14.0  4.0         32
1448  fff4e8465d1e12621bc361276b6217cf     21       8    10.0 -2.0         32
1449  fff4e8465d1e12621bc361276b6217cf     22      15    14.0  1.0         32
1450  fff4e8465d1e12621bc361276b6217cf     23      11     8.0  3.0         32

[1451 rows x 6 columns]


In [42]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error

In [43]:

# Extract the input features and target variable
X = final_df[['region_id', 'slots' ]]
y = final_df['gap']


# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [44]:
# Create the linear regression model
model = LinearRegression()

In [45]:
# Train the model on the training data
model.fit(X_train, y_train)

LinearRegression()

In [46]:
# Make predictions on the testing data
y_pred = model.predict(X_test)


In [47]:
# Calculate the mean squared error
mse = mean_squared_error(y_test, y_pred)
print(f'Mean squared error: {mse:.2f}')

Mean squared error: 24610.72


In [49]:
region_id = 12
time_slot = 3
prediction = model.predict(np.array([[region_id, time_slot]]))
print("Prediction of Linear regression: ", prediction[0])

Prediction of Linear regression:  10.314830364770716


c:\Users\shahzaib lptp\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but LinearRegression was fitted with feature names
  warnings.warn(


In [ ]:
import pickle
with open('linearRegression_model.pkl', 'wb') as file:
    pickle.dump(model, file)

In [ ]:
from sklearn.neighbors import KNeighborsClassifier
classifier = KNeighborsClassifier(n_neighbors=3)
classifier.fit(X_train, y_train)

KNeighborsClassifier(n_neighbors=3)

In [ ]:
y_pred = classifier.predict(X_test)

In [ ]:
# Calculate the mean squared error
mse2 = mean_squared_error(y_test, y_pred)
print(f'Mean squared error: {mse2:.2f}')

Mean squared error: 23951.98


In [ ]:
region_id = 12
time_slot = 3
prediction = classifier.predict(np.array([[region_id, time_slot]]))
print("Prediction of KNN: ", prediction)

Prediction of Linear regression:  [-98.]


c:\Users\shahzaib lptp\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(


In [ ]:
import tensorflow as tf
from sklearn.model_selection import train_test_split



In [ ]:
# Define the neural network model
model = tf.keras.Sequential([
    tf.keras.layers.Dense(64, input_dim=2, activation='relu'),
    tf.keras.layers.Dense(64, activation='relu'),
    tf.keras.layers.Dense(1)
])

# Compile and train the model
model.compile(optimizer='adam', loss='mean_squared_error', metrics=['mae'])
model.fit(X_train, y_train, epochs=10, batch_size=32, validation_split=0.2)

# Evaluate the model on the test data
test_loss, test_mae = model.evaluate(X_test, y_test)
print(f'Test loss: {test_loss:.4f}, Test MAE: {test_mae:.4f}')

# Use the model to make predictions on new data
region_id = 12
time_slot = 3
prediction = model.predict(np.array([[region_id, time_slot]]))
print(f'Predicted supply demand gap for region {region_id} at time slot {time_slot}: {prediction[0][0]:.2f}')

Epoch 1/10
29/29 [==============================] - 2s 14ms/step - loss: 41473.1758 - mae: 69.3456 - val_loss: 50868.7344 - val_mae: 74.1525
Epoch 2/10
29/29 [==============================] - 0s 4ms/step - loss: 40722.0586 - mae: 75.4491 - val_loss: 49947.3047 - val_mae: 81.0086
Epoch 3/10
29/29 [==============================] - 0s 3ms/step - loss: 40177.6836 - mae: 78.1065 - val_loss: 49519.2539 - val_mae: 83.4012
Epoch 4/10
29/29 [==============================] - 0s 4ms/step - loss: 39782.4922 - mae: 79.6206 - val_loss: 49273.1797 - val_mae: 83.3382
Epoch 5/10
29/29 [==============================] - 0s 4ms/step - loss: 39408.5547 - mae: 79.7627 - val_loss: 49042.0547 - val_mae: 84.4304
Epoch 6/10
29/29 [==============================] - 0s 4ms/step - loss: 39131.9961 - mae: 79.8306 - val_loss: 49081.1836 - val_mae: 82.6266
Epoch 7/10
29/29 [==============================] - 0s 3ms/step - loss: 38960.2070 - mae: 78.1234 - val_loss: 49018.2852 - val_mae: 84.2247
Epoch 8/10
29/29 [=

In [ ]:
with open('neuralNetwork_model.pkl', 'wb') as file:
    pickle.dump(model, file)